In [70]:
from python_speech_features import mfcc
import os

import pickle
import pandas as pd
import sklearn.metrics as maccuracy
import sklearn.metrics.pairwise as metrics
from sklearn import preprocessing

from tensorflow.keras.backend import argmax
from keras.optimizers import SGD


import numpy as np
import theano
import theano.tensor as T
import scipy.io.wavfile as wav
from theano.tensor.shared_randomstreams import RandomStreams

# SEQ 2 SEQ AUTO ENCODER

In [71]:



class SA(object):
    """ Long Short-Term Memory Sequence-to-Sequence Autoencoder
        (with peephole connections)
        References: [1] http://christianherta.de/lehre/dataScience/machineLearning/neuralNetworks/LSTM.php
                    [2] http://colah.github.io/posts/2015-08-Understanding-LSTMs/
    """

    def __init__(self, input, n_in, n_hidden, n_out, reverse=False, corruption_level=0.):

        self.n_in = n_in
        self.n_hidden = n_hidden
        self.n_out = n_out
        self.embeddings_list=[]


        assert self.n_in == self.n_out

        self.input = input

        numpy_rng = np.random.RandomState(123)
        self.theano_rng = RandomStreams(numpy_rng.randint(2 ** 30))
        self.corruption_level = corruption_level
        self.corrupted_input = self.theano_rng.binomial(
            size=self.input.shape, n=1,
            p=1 - corruption_level,
            dtype=theano.config.floatX
        ) * self.input

        def initialize_weights(shape):
            assert len(shape) == 2
            return np.asarray(
                a=np.random.uniform(
                    size=shape,
                    low=-.01,
                    high=.01
                ),
                dtype=theano.config.floatX
            )

        #######################################
        #######################################
        ##### Phase #1: Forward propagate #####
        #######################################
        #######################################

        # parameters for the input gates
        # x: x_{t} - current input frame
        # h: h_{t-1} - output of the previous frame x_{t-1}
        # c: c_{t-1} - cell state (not yet update)
        self.W_xi = theano.shared(value=initialize_weights((n_in, n_hidden)), name='W_xi', borrow=True)
        self.W_hi = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='W_hi', borrow=True)
        self.W_ci = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='W_ci', borrow=True)
        self.b_i = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='b_i', borrow=True)

        # parameters for the forget gates
        self.W_xf = theano.shared(value=initialize_weights((n_in, n_hidden)), name='W_xf', borrow=True)
        self.W_hf = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='W_hf', borrow=True)
        self.W_cf = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='W_cf', borrow=True)
        self.b_f = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='b_f', borrow=True)

        # parameters for the output gates
        # c: c_{t} - cell state (current cell state)
        self.W_xo = theano.shared(value=initialize_weights((n_in, n_hidden)), name='W_xo', borrow=True)
        self.W_ho = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='W_ho', borrow=True)
        self.W_co = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='W_co', borrow=True)
        self.b_o = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='b_o', borrow=True)

        # parameters for computing the values of cells (input)
        self.W_xc = theano.shared(value=initialize_weights((n_in, n_hidden)), name='W_xc', borrow=True)
        self.W_hc = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='W_hc', borrow=True)
        self.b_c = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='b_c', borrow=True)

        # initial values for memory cells
        self.c0 = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='c0', borrow=True)
        self.h0 = T.tanh(self.c0)

        self.params = [
            self.W_xi, self.W_hi, self.W_ci, self.b_i,  # input gates
            self.W_xf, self.W_hf, self.W_cf, self.b_f,  # forget gates
            self.W_xo, self.W_ho, self.W_co, self.b_o,  # output gates
            self.W_xc, self.W_hc, self.b_c,             # input memory cell
            self.c0                                     # initial values of memory cells
        ]

        def lstm_step(x_t, h_tm1, c_tm1):
            # For input, forget and output gates, we usually use the sigmoid function to
            # control "open" or "close".
            # The order of the implementation follows the article "Understanding LSTM Networks -- colah's blog"
            f_t = T.nnet.sigmoid(T.dot(x_t, self.W_xf) + T.dot(h_tm1, self.W_hf) + T.dot(c_tm1, self.W_cf) + self.b_f)
            i_t = T.nnet.sigmoid(T.dot(x_t, self.W_xi) + T.dot(h_tm1, self.W_hi) + T.dot(c_tm1, self.W_ci) + self.b_i)
            c_tilde_t = T.tanh(T.dot(x_t, self.W_xc) + T.dot(h_tm1, self.W_hc) + self.b_c)
            c_t = f_t * c_tm1 + i_t * c_tilde_t
            o_t = T.nnet.sigmoid(T.dot(x_t, self.W_xo) + T.dot(h_tm1, self.W_ho) + T.dot(c_t, self.W_co) + self.b_o)
            h_t = o_t * T.tanh(c_t)
            return [h_t, c_t]

        [self.h_vals, self.c_vals], _ = theano.scan(
            fn=lstm_step,
            sequences=self.corrupted_input,
            outputs_info=[self.h0, self.c0]
        )

        #################################
        #################################
        ##### Phase #2: Reconstruct #####
        #################################
        #################################

        # parameters for the input gates in reconstruction phase
        self.Wr_hi = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='Wr_hi', borrow=True)
        self.Wr_ci = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='Wr_ci', borrow=True)
        self.br_i = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='br_i', borrow=True)

        # parameters for the forget gates in reconstruction phase
        self.Wr_hf = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='Wr_hf', borrow=True)
        self.Wr_cf = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='Wr_cf', borrow=True)
        self.br_f = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='br_f', borrow=True)

        # parameters for the output gates in reconstruction phase
        self.Wr_ho = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='Wr_ho', borrow=True)
        self.Wr_co = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='Wr_co', borrow=True)
        self.br_o = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='br_o', borrow=True)

        # parameters for computing the values of cells (input) in reconstruction phase
        self.Wr_hc = theano.shared(value=initialize_weights((n_hidden, n_hidden)), name='Wr_hc', borrow=True)
        self.br_c = theano.shared(value=np.zeros((n_hidden,), dtype=theano.config.floatX), name='br_c', borrow=True)

        # parameters for the output (prediction) in reconstruction phase
        self.Wr_out = theano.shared(value=initialize_weights((n_hidden, n_out)), name='Wr_out', borrow=True)
        self.br_out = theano.shared(value=np.zeros((n_out,), dtype=theano.config.floatX), name='br_out', borrow=True)

        # add the parameters for reconstruction phase
        self.params.extend([
            self.Wr_hi, self.Wr_ci, self.br_i,
            self.Wr_hf, self.Wr_cf, self.br_f,
            self.Wr_ho, self.Wr_co, self.br_o,
            self.Wr_hc, self.br_c,
            self.Wr_out, self.br_out
        ])

        self.Wr_xi = theano.shared(value=initialize_weights((n_out, n_hidden)), name='Wr_xi', borrow=True)
        self.Wr_xf = theano.shared(value=initialize_weights((n_out, n_hidden)), name='Wr_xf', borrow=True)
        self.Wr_xo = theano.shared(value=initialize_weights((n_out, n_hidden)), name='Wr_xo', borrow=True)
        self.Wr_xc = theano.shared(value=initialize_weights((n_out, n_hidden)), name='Wr_xc', borrow=True)
        self.params.extend([self.Wr_xi, self.Wr_xf, self.Wr_xo, self.Wr_xc])

        def lstm_reconstruct_step(x_t, h_tm1, c_tm1):
            f_t = T.nnet.sigmoid(T.dot(x_t, self.Wr_xf) + T.dot(h_tm1, self.Wr_hf) + T.dot(c_tm1, self.Wr_cf) + self.br_f)
            i_t = T.nnet.sigmoid(T.dot(x_t, self.Wr_xi) + T.dot(h_tm1, self.Wr_hi) + T.dot(c_tm1, self.Wr_ci) + self.br_i)
            c_tilde_t = T.tanh(T.dot(x_t, self.Wr_xc) + T.dot(h_tm1, self.Wr_hc) + self.br_c)
            c_t = f_t * c_tm1 + i_t * c_tilde_t
            o_t = T.nnet.sigmoid(T.dot(x_t, self.Wr_xo) + T.dot(h_tm1, self.Wr_ho) + T.dot(c_t, self.Wr_co) + self.br_o)
            h_t = o_t * T.tanh(c_t)
            y_t = T.dot(h_t, self.Wr_out) + self.br_out
            return [y_t, h_t, c_t]

        # Start of reconstructed sequence: act as constant zero vector
        SORS = theano.shared(value=np.zeros((n_in,), dtype=theano.config.floatX), name='SORS', borrow=True)
        [self.yr_vals, self.hr_vals, self.cr_vals], _ = theano.scan(
            fn=lstm_reconstruct_step,
            outputs_info=[SORS, self.h_vals[-1], self.c_vals[-1]],
            n_steps=self.input.shape[0]
        )

        if reverse:
            self.mse = T.mean((self.yr_vals[::-1] - self.input) ** 2)#same yr_vals list in reverse order.
            #for reference of above :https://docs.python.org/release/2.3.5/whatsnew/section-slices.html
        else:
            self.mse = T.mean((self.yr_vals - self.input) ** 2)
    def create_embeddings(self,input_words,feature_range):
        n_inputs=len(input_words)
        embeddings_list=[]
        fmin,fmax=feature_range
        for i in range(n_inputs):
            input_words[i]=np.asarray(
                    a=(input_words[i]-fmin)/(fmax-fmin)*2-1,
                    dtype='float32')
        word_embeddings = theano.function(
            #Returns:	a callable object that will compute the outputs (given the inputs) and 
            #update the implicit function arguments according to the updates.
            inputs=[self.input],
            outputs=self.h_vals,
            name='word_embeddings' )
        print("embeddings...")
        x=word_embeddings(input_words)
        return x
    """  train_order = np.arange(n_inputs)
        np.random.shuffle(train_order)
        for index in train_order:
            print(index)
            embeddings_list.append( word_embeddings(input_words[index])[-1])"""

    def train(self, X_train, X_test, n_epochs, learning_rate, save_steps, feature_range):

        n_train = len(X_train)
        n_test = len(X_test)

        # Linearly scale all values to range [-1, 1]
        f_min, f_max = feature_range
        for i in range(n_train):
            X_train[i] = np.asarray(
                a=(X_train[i] - f_min) / (f_max - f_min) * 2 - 1,
                dtype='float32'
            )
           
        for i in range(n_test):
            X_test[i] = np.asarray(
                a=(X_test[i] - f_min) / (f_max - f_min) * 2 - 1,
                dtype='float32'
            )

        print ('compiling theano training functions ...')
        # define the objective function to be minimized
        objective_func = self.mse
        print(X_train.shape)
        # compute the gradients of the objective function w.r.t. self.params using BPTT
        gparams = T.grad(cost=objective_func, wrt=self.params)
        updates = [
            (param, param - learning_rate * gparam)
            
            for param, gparam in zip(self.params, gparams)
        ]

        # compiling a Theano function `train_model` that returns the
        # cost, but in the same time updates the parameter of the
        # model based on the rules defined in `updates`
        train_model = theano.function(
            #Returns:	a callable object that will compute the outputs (given the inputs) and 
            #update the implicit function arguments according to the updates.
            inputs=[self.input],
            outputs=objective_func * ((f_max - f_min) ** 2) / 4,
            updates=updates,
            name='train_model',
            #mode='DebugMode',
        )

        test_model = theano.function(
            inputs=[self.input],
            outputs=objective_func * ((f_max - f_min) ** 2) / 4,
            name='test_model'
        )

        if self.corruption_level > 0:
            print ('\nBe cautious! The reconstruction error of test_model is computed in terms of noisy input!\n')

        reconstruct_model = theano.function(
            #Returns:	a callable object that will compute the outputs (given the inputs) and 
            #update the implicit function arguments according to the updates.
            inputs=[self.input],
            outputs=self.yr_vals,
            name='reconstruct_model'
        )

        print( 'training the SA model ...')
        # optimize the model parameters using stochastic gradient descent
        train_order = np.arange(n_train)
        for epoch in range(n_epochs):
            total_batch_cost = 0.
            print ('\nepoch #%d' % (epoch + 1))
            np.random.shuffle(train_order)
            for index in train_order:
                #print(index)
                batch_cost = train_model(X_train[index])
                total_batch_cost += batch_cost
            print ('average train batch cost = %f' % (total_batch_cost / n_train))
            test_batch_cost = np.zeros(n_test)
            for index in range(n_test):
                test_batch_cost[index] = test_model(X_test[index])
            print ('average test batch cost = %f' % (np.mean(test_batch_cost)))
            if (epoch + 1) % save_steps == 0:
                with open('lstmae.' + str(self.n_hidden) + '.' + str(epoch + 1) + '.pkl', 'wb') as f:
                    pickle.dump(self, f, protocol=pickle.HIGHEST_PROTOCOL)
        # save the final model
        with open('lstmae.' + str(self.n_hidden) + '.final.pkl', 'wb') as f:
            pickle.dump(self, f, protocol=pickle.HIGHEST_PROTOCOL)

In [72]:
x=T.matrix('x')
v_in=T.vector('v_in')
sa1=SA(x,13,150,13)
x.type

TensorType(float64, matrix)

# MFCC FEATURES FOR TRAINING 

In [73]:
timit="word_wise_data/train_words"
train_labels=[]
list=[]
timit_db=[os.path.join(timit,p) for p in sorted(os.listdir(timit))]
for i in range(len(timit_db)):
    word=timit_db[i].split("\\")[1]
    word_from_every_speaker_path=[os.path.join(timit_db[i],p) for p in sorted(os.listdir(timit_db[i]))]
    for i in range(len(word_from_every_speaker_path)):
        (rate,sig) = wav.read(word_from_every_speaker_path[i])
        if(sig.shape[0]!=0):
            mfcc_feat= mfcc(sig,rate)
            list.append(mfcc_feat)
            train_labels.append(word)
            print(word_from_every_speaker_path[i].split("\\")[2])
x_train=np.asarray(list)

FAEM0_all.WAV
FAJW0_all.WAV
FALK0_all.WAV
FALR0_all.WAV
FAPB0_all.WAV
FBAS0_all.WAV
FBCG1_all.WAV
FBCH0_all.WAV
FBJL0_all.WAV
FBLV0_all.WAV
FBMH0_all.WAV
FBMJ0_all.WAV
FCAG0_all.WAV
FCAJ0_all.WAV
FCDR1_all.WAV
FCEG0_all.WAV
FCJF0_all.WAV
FCJS0_all.WAV
FCKE0_all.WAV
FCLT0_all.WAV
FCMG0_all.WAV
FCMM0_all.WAV
FCRZ0_all.WAV
FCYL0_all.WAV
FDAS1_all.WAV
FDAW0_all.WAV
FDFB0_all.WAV
FDJH0_all.WAV
FDKN0_all.WAV
FDML0_all.WAV
FDMY0_all.WAV
FDNC0_all.WAV
FDTD0_all.WAV
FDXW0_all.WAV
FEAC0_all.WAV
FEAR0_all.WAV
FECD0_all.WAV
FEEH0_all.WAV
FEME0_all.WAV
FETB0_all.WAV
FEXM0_all.WAV
FGCS0_all.WAV
FGDP0_all.WAV
FGMB0_all.WAV
FGRW0_all.WAV
FHLM0_all.WAV
FHXS0_all.WAV
FJDM2_all.WAV
FJEN0_all.WAV
FJHK0_all.WAV
FJKL0_all.WAV
FJLG0_all.WAV
FJLR0_all.WAV
FJRB0_all.WAV
FJRP1_all.WAV
FJSK0_all.WAV
FJSP0_all.WAV
FJWB1_all.WAV
FJXM0_all.WAV
FJXP0_all.WAV
FKAA0_all.WAV
FKDE0_all.WAV
FKDW0_all.WAV
FKFB0_all.WAV
FKKH0_all.WAV
FKLC0_all.WAV
FKLC1_all.WAV
FKLH0_all.WAV
FKSR0_all.WAV
FLAC0_all.WAV
FLAG0_all.WAV
FLEH0_

MBJV0_an.WAV
MBMA0_an.WAV
MBMA1_an.WAV
MBML0_an.WAV
MBOM0_an.WAV
MBSB0_an.WAV
MBTH0_an.WAV
MBWP0_an.WAV
MCAE0_an.WAV
MCAL0_an.WAV
MCDC0_an.WAV
MCDD0_an.WAV
MCDR0_an.WAV
MCEF0_an.WAV
MCEW0_an.WAV
MCHL0_an.WAV
MCLK0_an.WAV
MCLM0_an.WAV
MCPM0_an.WAV
MCRE0_an.WAV
MCSS0_an.WAV
MCTH0_an.WAV
MCTM0_an.WAV
MCXM0_an.WAV
MDAC0_an.WAV
MDAS0_an.WAV
MDBB1_an.WAV
MDBP0_an.WAV
MDCD0_an.WAV
MDCM0_an.WAV
MDDC0_an.WAV
MDED0_an.WAV
MDEF0_an.WAV
MDEM0_an.WAV
MDHL0_an.WAV
MDHS0_an.WAV
MDJM0_an.WAV
MDKS0_an.WAV
MDLB0_an.WAV
MDLC0_an.WAV
MDLC1_an.WAV
MDLC2_an.WAV
MDLH0_an.WAV
MDLM0_an.WAV
MDLR0_an.WAV
MDLR1_an.WAV
MDMA0_an.WAV
MDMT0_an.WAV
MDNS0_an.WAV
MDPB0_an.WAV
MDPK0_an.WAV
MDPS0_an.WAV
MDRD0_an.WAV
MDSJ0_an.WAV
MDSS0_an.WAV
MDSS1_an.WAV
MDTB0_an.WAV
MDWD0_an.WAV
MDWH0_an.WAV
MDWM0_an.WAV
MEAL0_an.WAV
MEDR0_an.WAV
MEFG0_an.WAV
MEGJ0_an.WAV
MEJL0_an.WAV
MEJS0_an.WAV
MESG0_an.WAV
MESJ0_an.WAV
MEWM0_an.WAV
MFER0_an.WAV
MFMC0_an.WAV
MFRM0_an.WAV
MFWK0_an.WAV
MFXS0_an.WAV
MFXV0_an.WAV
MGAF0_an.WAV
MGAG0_an.WAV

MPFU0_ask.WAV
MPGH0_ask.WAV
MPGR0_ask.WAV
MPGR1_ask.WAV
MPMB0_ask.WAV
MPPC0_ask.WAV
MPRB0_ask.WAV
MPRD0_ask.WAV
MPRK0_ask.WAV
MPRT0_ask.WAV
MPSW0_ask.WAV
MRAB0_ask.WAV
MRAB1_ask.WAV
MRAI0_ask.WAV
MRAM0_ask.WAV
MRAV0_ask.WAV
MRBC0_ask.WAV
MRCG0_ask.WAV
MRCW0_ask.WAV
MRDD0_ask.WAV
MRDM0_ask.WAV
MRDS0_ask.WAV
MREE0_ask.WAV
MREH1_ask.WAV
MREM0_ask.WAV
MREW1_ask.WAV
MRFK0_ask.WAV
MRFL0_ask.WAV
MRGM0_ask.WAV
MRGS0_ask.WAV
MRHL0_ask.WAV
MRJB1_ask.WAV
MRJH0_ask.WAV
MRJM0_ask.WAV
MRJM1_ask.WAV
MRJT0_ask.WAV
MRKM0_ask.WAV
MRLD0_ask.WAV
MRLJ0_ask.WAV
MRLJ1_ask.WAV
MRLK0_ask.WAV
MRLR0_ask.WAV
MRMB0_ask.WAV
MRMG0_ask.WAV
MRMH0_ask.WAV
MRML0_ask.WAV
MRMS0_ask.WAV
MRPC1_ask.WAV
MRRE0_ask.WAV
MRSO0_ask.WAV
MRSP0_ask.WAV
MRTC0_ask.WAV
MRTJ0_ask.WAV
MRVG0_ask.WAV
MRWA0_ask.WAV
MRWS0_ask.WAV
MRXB0_ask.WAV
MSAH1_ask.WAV
MSAS0_ask.WAV
MSAT0_ask.WAV
MSAT1_ask.WAV
MSDB0_ask.WAV
MSDH0_ask.WAV
MSDS0_ask.WAV
MSEM1_ask.WAV
MSES0_ask.WAV
MSFH0_ask.WAV
MSFV0_ask.WAV
MSJK0_ask.WAV
MSMC0_ask.WAV
MSMR0_ask.WAV
MSMS0_

MWSH0_carry.WAV
MZMB0_carry.WAV
FAEM0_dark.WAV
FAJW0_dark.WAV
FALK0_dark.WAV
FALR0_dark.WAV
FAPB0_dark.WAV
FBAS0_dark.WAV
FBCG1_dark.WAV
FBCH0_dark.WAV
FBJL0_dark.WAV
FBLV0_dark.WAV
FBMH0_dark.WAV
FBMJ0_dark.WAV
FCAG0_dark.WAV
FCAJ0_dark.WAV
FCDR1_dark.WAV
FCEG0_dark.WAV
FCJF0_dark.WAV
FCJS0_dark.WAV
FCKE0_dark.WAV
FCLT0_dark.WAV
FCMG0_dark.WAV
FCMM0_dark.WAV
FCRZ0_dark.WAV
FCYL0_dark.WAV
FDAS1_dark.WAV
FDAW0_dark.WAV
FDFB0_dark.WAV
FDJH0_dark.WAV
FDKN0_dark.WAV
FDML0_dark.WAV
FDMY0_dark.WAV
FDNC0_dark.WAV
FDTD0_dark.WAV
FDXW0_dark.WAV
FEAC0_dark.WAV
FEAR0_dark.WAV
FECD0_dark.WAV
FEEH0_dark.WAV
FEME0_dark.WAV
FETB0_dark.WAV
FEXM0_dark.WAV
FGCS0_dark.WAV
FGDP0_dark.WAV
FGMB0_dark.WAV
FGRW0_dark.WAV
FHLM0_dark.WAV
FHXS0_dark.WAV
FJDM2_dark.WAV
FJEN0_dark.WAV
FJHK0_dark.WAV
FJKL0_dark.WAV
FJLG0_dark.WAV
FJLR0_dark.WAV
FJRB0_dark.WAV
FJRP1_dark.WAV
FJSK0_dark.WAV
FJSP0_dark.WAV
FJWB1_dark.WAV
FJXM0_dark.WAV
FJXP0_dark.WAV
FKAA0_dark.WAV
FKDE0_dark.WAV
FKDW0_dark.WAV
FKFB0_dark.WAV
FKKH0_da

MDLC1_don't.WAV
MDLC2_don't.WAV
MDLH0_don't.WAV
MDLM0_don't.WAV
MDLR0_don't.WAV
MDLR1_don't.WAV
MDMA0_don't.WAV
MDMT0_don't.WAV
MDNS0_don't.WAV
MDPB0_don't.WAV
MDPK0_don't.WAV
MDPS0_don't.WAV
MDRD0_don't.WAV
MDSJ0_don't.WAV
MDSS0_don't.WAV
MDSS1_don't.WAV
MDTB0_don't.WAV
MDWD0_don't.WAV
MDWH0_don't.WAV
MDWM0_don't.WAV
MEAL0_don't.WAV
MEDR0_don't.WAV
MEFG0_don't.WAV
MEGJ0_don't.WAV
MEJL0_don't.WAV
MEJS0_don't.WAV
MESG0_don't.WAV
MESJ0_don't.WAV
MEWM0_don't.WAV
MFER0_don't.WAV
MFMC0_don't.WAV
MFRM0_don't.WAV
MFWK0_don't.WAV
MFXS0_don't.WAV
MFXV0_don't.WAV
MGAF0_don't.WAV
MGAG0_don't.WAV
MGAK0_don't.WAV
MGAR0_don't.WAV
MGAW0_don't.WAV
MGES0_don't.WAV
MGJC0_don't.WAV
MGRL0_don't.WAV
MGRP0_don't.WAV
MGSH0_don't.WAV
MGSL0_don't.WAV
MGXP0_don't.WAV
MHBS0_don't.WAV
MHIT0_don't.WAV
MHJB0_don't.WAV
MHMG0_don't.WAV
MHMR0_don't.WAV
MHRM0_don't.WAV
MHXL0_don't.WAV
MILB0_don't.WAV
MJAC0_don't.WAV
MJAE0_don't.WAV
MJAI0_don't.WAV
MJBG0_don't.WAV
MJDA0_don't.WAV
MJDC0_don't.WAV
MJDE0_don't.WAV
MJDG0_do

...

FDXW0_that.WAV
FEAC0_that.WAV
FEAR0_that.WAV
FECD0_that.WAV
FEEH0_that.WAV
FEME0_that.WAV
FETB0_that.WAV
FEXM0_that.WAV
FGCS0_that.WAV
FGDP0_that.WAV
FGMB0_that.WAV
FGRW0_that.WAV
FHLM0_that.WAV
FHXS0_that.WAV
FJDM2_that.WAV
FJEN0_that.WAV
FJHK0_that.WAV
FJKL0_that.WAV
FJLG0_that.WAV
FJLR0_that.WAV
FJRB0_that.WAV
FJRP1_that.WAV
FJSK0_that.WAV
FJSP0_that.WAV
FJWB1_that.WAV
FJXM0_that.WAV
FJXP0_that.WAV
FKAA0_that.WAV
FKDE0_that.WAV
FKDW0_that.WAV
FKFB0_that.WAV
FKKH0_that.WAV
FKLC0_that.WAV
FKLC1_that.WAV
FKLH0_that.WAV
FKSR0_that.WAV
FLAC0_that.WAV
FLAG0_that.WAV
FLEH0_that.WAV
FLET0_that.WAV
FLHD0_that.WAV
FLJA0_that.WAV
FLJD0_that.WAV
FLJG0_that.WAV
FLKM0_that.WAV
FLMA0_that.WAV
FLMC0_that.WAV
FLMK0_that.WAV
FLOD0_that.WAV
FLTM0_that.WAV
FMAH1_that.WAV
FMBG0_that.WAV
FMEM0_that.WAV
FMJB0_that.WAV
FMJF0_that.WAV
FMJU0_that.WAV
FMKC0_that.WAV
FMKF0_that.WAV
FMMH0_that.WAV
FMPG0_that.WAV
FNKL0_that.WAV
FNTB0_that.WAV
FPAB1_that.WAV
FPAC0_that.WAV
FPAD0_that.WAV
FPAF0_that.WAV
FPAZ0_that

MDRD0_to.WAV
MDSJ0_to.WAV
MDSS0_to.WAV
MDSS1_to.WAV
MDTB0_to.WAV
MDWD0_to.WAV
MDWH0_to.WAV
MDWM0_to.WAV
MEDR0_to.WAV
MEFG0_to.WAV
MEGJ0_to.WAV
MEJL0_to.WAV
MEJS0_to.WAV
MESG0_to.WAV
MESJ0_to.WAV
MEWM0_to.WAV
MFER0_to.WAV
MFMC0_to.WAV
MFRM0_to.WAV
MFWK0_to.WAV
MFXS0_to.WAV
MFXV0_to.WAV
MGAF0_to.WAV
MGAG0_to.WAV
MGAK0_to.WAV
MGAR0_to.WAV
MGAW0_to.WAV
MGES0_to.WAV
MGJC0_to.WAV
MGRL0_to.WAV
MGRP0_to.WAV
MGSH0_to.WAV
MGSL0_to.WAV
MGXP0_to.WAV
MHBS0_to.WAV
MHIT0_to.WAV
MHMG0_to.WAV
MHMR0_to.WAV
MHRM0_to.WAV
MHXL0_to.WAV
MILB0_to.WAV
MJAC0_to.WAV
MJAE0_to.WAV
MJAI0_to.WAV
MJBG0_to.WAV
MJDA0_to.WAV
MJDC0_to.WAV
MJDE0_to.WAV
MJDG0_to.WAV
MJDM0_to.WAV
MJEB0_to.WAV
MJEB1_to.WAV
MJEE0_to.WAV
MJFH0_to.WAV
MJFR0_to.WAV
MJHI0_to.WAV
MJJB0_to.WAV
MJJJ0_to.WAV
MJJM0_to.WAV
MJKR0_to.WAV
MJLB0_to.WAV
MJLG1_to.WAV
MJLS0_to.WAV
MJMA0_to.WAV
MJMD0_to.WAV
MJMM0_to.WAV
MJPG0_to.WAV
MJPM0_to.WAV
MJPM1_to.WAV
MJRA0_to.WAV
MJRG0_to.WAV
MJRH0_to.WAV
MJRH1_to.WAV
MJRK0_to.WAV
MJRP0_to.WAV
MJSR0_to.WAV
MJWG0_to.WAV

MVRW0_wash.WAV
MWAC0_wash.WAV
MWAD0_wash.WAV
MWAR0_wash.WAV
MWCH0_wash.WAV
MWDK0_wash.WAV
MWEM0_wash.WAV
MWGR0_wash.WAV
MWRE0_wash.WAV
MWRP0_wash.WAV
MWSB0_wash.WAV
MWSH0_wash.WAV
MZMB0_wash.WAV
FAEM0_water.WAV
FAJW0_water.WAV
FALK0_water.WAV
FALR0_water.WAV
FAPB0_water.WAV
FBAS0_water.WAV
FBCG1_water.WAV
FBCH0_water.WAV
FBJL0_water.WAV
FBLV0_water.WAV
FBMH0_water.WAV
FBMJ0_water.WAV
FCAG0_water.WAV
FCAJ0_water.WAV
FCDR1_water.WAV
FCEG0_water.WAV
FCJF0_water.WAV
FCJS0_water.WAV
FCKE0_water.WAV
FCLT0_water.WAV
FCMG0_water.WAV
FCMM0_water.WAV
FCRZ0_water.WAV
FCYL0_water.WAV
FDAS1_water.WAV
FDAW0_water.WAV
FDFB0_water.WAV
FDJH0_water.WAV
FDKN0_water.WAV
FDML0_water.WAV
FDMY0_water.WAV
FDNC0_water.WAV
FDTD0_water.WAV
FDXW0_water.WAV
FEAC0_water.WAV
FEAR0_water.WAV
FECD0_water.WAV
FEEH0_water.WAV
FEME0_water.WAV
FETB0_water.WAV
FEXM0_water.WAV
FGCS0_water.WAV
FGDP0_water.WAV
FGMB0_water.WAV
FGRW0_water.WAV
FHLM0_water.WAV
FHXS0_water.WAV
FJDM2_water.WAV
FJEN0_water.WAV
FJHK0_water.WAV
FJKL0

MADC0_year.WAV
MADD0_year.WAV
MAEB0_year.WAV
MAEO0_year.WAV
MAFM0_year.WAV
MAJP0_year.WAV
MAKB0_year.WAV
MAKR0_year.WAV
MAPV0_year.WAV
MARC0_year.WAV
MARW0_year.WAV
MBAR0_year.WAV
MBBR0_year.WAV
MBCG0_year.WAV
MBEF0_year.WAV
MBGT0_year.WAV
MBJV0_year.WAV
MBMA0_year.WAV
MBMA1_year.WAV
MBML0_year.WAV
MBOM0_year.WAV
MBSB0_year.WAV
MBTH0_year.WAV
MBWP0_year.WAV
MCAE0_year.WAV
MCAL0_year.WAV
MCDC0_year.WAV
MCDD0_year.WAV
MCDR0_year.WAV
MCEF0_year.WAV
MCEW0_year.WAV
MCHL0_year.WAV
MCLK0_year.WAV
MCLM0_year.WAV
MCPM0_year.WAV
MCRE0_year.WAV
MCSS0_year.WAV
MCTH0_year.WAV
MCTM0_year.WAV
MCXM0_year.WAV
MDAC0_year.WAV
MDAS0_year.WAV
MDBB1_year.WAV
MDBP0_year.WAV
MDCD0_year.WAV
MDCM0_year.WAV
MDDC0_year.WAV
MDED0_year.WAV
MDEF0_year.WAV
MDEM0_year.WAV
MDHL0_year.WAV
MDHS0_year.WAV
MDJM0_year.WAV
MDKS0_year.WAV
MDLB0_year.WAV
MDLC0_year.WAV
MDLC1_year.WAV
MDLC2_year.WAV
MDLH0_year.WAV
MDLM0_year.WAV
MDLR0_year.WAV
MDLR1_year.WAV
MDMA0_year.WAV
MDMT0_year.WAV
MDNS0_year.WAV
MDPB0_year.WAV
MDPK0_year

MJEB1_your.WAV
MJEE0_your.WAV
MJFH0_your.WAV
MJFR0_your.WAV
MJHI0_your.WAV
MJJB0_your.WAV
MJJJ0_your.WAV
MJJM0_your.WAV
MJKR0_your.WAV
MJLB0_your.WAV
MJLG1_your.WAV
MJLS0_your.WAV
MJMA0_your.WAV
MJMD0_your.WAV
MJMM0_your.WAV
MJPG0_your.WAV
MJPM0_your.WAV
MJPM1_your.WAV
MJRA0_your.WAV
MJRG0_your.WAV
MJRH0_your.WAV
MJRH1_your.WAV
MJRK0_your.WAV
MJRP0_your.WAV
MJSR0_your.WAV
MJWG0_your.WAV
MJWS0_your.WAV
MJWT0_your.WAV
MJXA0_your.WAV
MJXL0_your.WAV
MKAG0_your.WAV
MKAH0_your.WAV
MKAJ0_your.WAV
MKAM0_your.WAV
MKDB0_your.WAV
MKDD0_your.WAV
MKDT0_your.WAV
MKES0_your.WAV
MKJO0_your.WAV
MKLN0_your.WAV
MKLR0_your.WAV
MKLS0_your.WAV
MKLS1_your.WAV
MKLW0_your.WAV
MKRG0_your.WAV
MKXL0_your.WAV
MLBC0_your.WAV
MLEL0_your.WAV
MLJC0_your.WAV
MLJH0_your.WAV
MLNS0_your.WAV
MLSH0_your.WAV
MMAA0_your.WAV
MMAB1_your.WAV
MMAG0_your.WAV
MMAM0_your.WAV
MMAR0_your.WAV
MMBS0_your.WAV
MMCC0_your.WAV
MMDB0_your.WAV
MMDG0_your.WAV
MMDM0_your.WAV
MMDM1_your.WAV
MMDS0_your.WAV
MMEA0_your.WAV
MMEB0_your.WAV
MMGC0_your

In [81]:
x_train[0].shape

(17, 13)

In [74]:
timit="word_wise_data/test_words"
test_labels=[]
list=[]
timit_db=[os.path.join(timit,p) for p in sorted(os.listdir(timit))]
for i in range(len(timit_db)):
    #word=timit_db[i].split("\\")[3]
    word_from_every_speaker_path=[os.path.join(timit_db[i],p) for p in sorted(os.listdir(timit_db[i]))]
    for i in range(len(word_from_every_speaker_path)):
        (rate,sig) = wav.read(word_from_every_speaker_path[i])
        if(sig.shape[0]!=0):
            mfcc_feat= mfcc(sig,rate)
            list.append(mfcc_feat)
            print(word_from_every_speaker_path[i].split("\\")[2])
x_test=np.asarray(list)

FADG0_all.WAV
FAKS0_all.WAV
FASW0_all.WAV
FAWF0_all.WAV
FCAL1_all.WAV
FCAU0_all.WAV
FCFT0_all.WAV
FCMH0_all.WAV
FCMH1_all.WAV
FCMR0_all.WAV
FCRH0_all.WAV
FDAC1_all.WAV
FDHC0_all.WAV
FDMS0_all.WAV
FDRD1_all.WAV
FDRW0_all.WAV
FEDW0_all.WAV
FELC0_all.WAV
FGJD0_all.WAV
FGMD0_all.WAV
FGWR0_all.WAV
FHES0_all.WAV
FHEW0_all.WAV
FISB0_all.WAV
FJAS0_all.WAV
FJCS0_all.WAV
FJEM0_all.WAV
FJLM0_all.WAV
FJMG0_all.WAV
FJRE0_all.WAV
FJSA0_all.WAV
FJSJ0_all.WAV
FJWB0_all.WAV
FKMS0_all.WAV
FLAS0_all.WAV
FLBW0_all.WAV
FLKD0_all.WAV
FLNH0_all.WAV
FMAF0_all.WAV
FMAH0_all.WAV
FMCM0_all.WAV
FMGD0_all.WAV
FMLD0_all.WAV
FMML0_all.WAV
FNLP0_all.WAV
FNMR0_all.WAV
FPAS0_all.WAV
FPKT0_all.WAV
FRAM1_all.WAV
FREW0_all.WAV
FRNG0_all.WAV
FSEM0_all.WAV
FSLB1_all.WAV
FSXA0_all.WAV
FTLH0_all.WAV
FUTB0_all.WAV
MABW0_all.WAV
MAHH0_all.WAV
MAJC0_all.WAV
MBDG0_all.WAV
MBJK0_all.WAV
MBNS0_all.WAV
MBPM0_all.WAV
MBWM0_all.WAV
MCCS0_all.WAV
MCEM0_all.WAV
MCHH0_all.WAV
MCMB0_all.WAV
MCMJ0_all.WAV
MCRC0_all.WAV
MCSH0_all.WAV
MCTT0_

FDAC1_dark.WAV
FDHC0_dark.WAV
FDMS0_dark.WAV
FDRD1_dark.WAV
FDRW0_dark.WAV
FEDW0_dark.WAV
FELC0_dark.WAV
FGJD0_dark.WAV
FGMD0_dark.WAV
FGWR0_dark.WAV
FHES0_dark.WAV
FHEW0_dark.WAV
FISB0_dark.WAV
FJAS0_dark.WAV
FJCS0_dark.WAV
FJEM0_dark.WAV
FJLM0_dark.WAV
FJMG0_dark.WAV
FJRE0_dark.WAV
FJSA0_dark.WAV
FJSJ0_dark.WAV
FJWB0_dark.WAV
FKMS0_dark.WAV
FLAS0_dark.WAV
FLBW0_dark.WAV
FLKD0_dark.WAV
FLNH0_dark.WAV
FMAF0_dark.WAV
FMAH0_dark.WAV
FMCM0_dark.WAV
FMGD0_dark.WAV
FMLD0_dark.WAV
FMML0_dark.WAV
FNLP0_dark.WAV
FNMR0_dark.WAV
FPAS0_dark.WAV
FPKT0_dark.WAV
FRAM1_dark.WAV
FREW0_dark.WAV
FRNG0_dark.WAV
FSEM0_dark.WAV
FSLB1_dark.WAV
FSXA0_dark.WAV
FTLH0_dark.WAV
FUTB0_dark.WAV
MABW0_dark.WAV
MAHH0_dark.WAV
MAJC0_dark.WAV
MBDG0_dark.WAV
MBJK0_dark.WAV
MBNS0_dark.WAV
MBPM0_dark.WAV
MBWM0_dark.WAV
MCCS0_dark.WAV
MCEM0_dark.WAV
MCHH0_dark.WAV
MCMB0_dark.WAV
MCMJ0_dark.WAV
MCRC0_dark.WAV
MCSH0_dark.WAV
MCTT0_dark.WAV
MCTW0_dark.WAV
MDAB0_dark.WAV
MDAC2_dark.WAV
MDAW1_dark.WAV
MDBB0_dark.WAV
MDLD0_dark

MBJK0_had.WAV
MBNS0_had.WAV
MBPM0_had.WAV
MBWM0_had.WAV
MCCS0_had.WAV
MCEM0_had.WAV
MCHH0_had.WAV
MCMB0_had.WAV
MCMJ0_had.WAV
MCRC0_had.WAV
MCSH0_had.WAV
MCTT0_had.WAV
MCTW0_had.WAV
MDAB0_had.WAV
MDAC2_had.WAV
MDAW1_had.WAV
MDBB0_had.WAV
MDLD0_had.WAV
MDLF0_had.WAV
MDLS0_had.WAV
MDRB0_had.WAV
MDRM0_had.WAV
MDSC0_had.WAV
MDVC0_had.WAV
MDWA0_had.WAV
MDWK0_had.WAV
MERS0_had.WAV
MESD0_had.WAV
MFGK0_had.WAV
MGJF0_had.WAV
MGLB0_had.WAV
MGMM0_had.WAV
MGRT0_had.WAV
MGWT0_had.WAV
MHPG0_had.WAV
MJAR0_had.WAV
MJBR0_had.WAV
MJDH0_had.WAV
MJDM1_had.WAV
MJES0_had.WAV
MJFC0_had.WAV
MJJG0_had.WAV
MJLN0_had.WAV
MJMP0_had.WAV
MJRF0_had.WAV
MJSW0_had.WAV
MJTC0_had.WAV
MJTH0_had.WAV
MJVW0_had.WAV
MKCH0_had.WAV
MKCL0_had.WAV
MKDR0_had.WAV
MKJL0_had.WAV
MKLT0_had.WAV
MLIH0_had.WAV
MLJB0_had.WAV
MLLL0_had.WAV
MLNT0_had.WAV
MMAB0_had.WAV
MMDB1_had.WAV
MMDH0_had.WAV
MMDM2_had.WAV
MMJR0_had.WAV
MMWH0_had.WAV
MNJM0_had.WAV
MNLS0_had.WAV
MPAB0_had.WAV
MPAM0_had.WAV
MPAM1_had.WAV
MPCS0_had.WAV
MPDF0_had.WAV
MPGL0_

MDAW1_oily.WAV
MDBB0_oily.WAV
MDLD0_oily.WAV
MDLF0_oily.WAV
MDLS0_oily.WAV
MDRB0_oily.WAV
MDRM0_oily.WAV
MDSC0_oily.WAV
MDVC0_oily.WAV
MDWA0_oily.WAV
MDWK0_oily.WAV
MERS0_oily.WAV
MESD0_oily.WAV
MFGK0_oily.WAV
MGJF0_oily.WAV
MGLB0_oily.WAV
MGMM0_oily.WAV
MGRT0_oily.WAV
MGWT0_oily.WAV
MHPG0_oily.WAV
MJAR0_oily.WAV
MJBR0_oily.WAV
MJDH0_oily.WAV
MJDM1_oily.WAV
MJES0_oily.WAV
MJFC0_oily.WAV
MJJG0_oily.WAV
MJLN0_oily.WAV
MJMP0_oily.WAV
MJRF0_oily.WAV
MJSW0_oily.WAV
MJTC0_oily.WAV
MJTH0_oily.WAV
MJVW0_oily.WAV
MKCH0_oily.WAV
MKCL0_oily.WAV
MKDR0_oily.WAV
MKJL0_oily.WAV
MKLT0_oily.WAV
MLIH0_oily.WAV
MLJB0_oily.WAV
MLLL0_oily.WAV
MLNT0_oily.WAV
MMAB0_oily.WAV
MMDB1_oily.WAV
MMDH0_oily.WAV
MMDM2_oily.WAV
MMJR0_oily.WAV
MMWH0_oily.WAV
MNJM0_oily.WAV
MNLS0_oily.WAV
MPAB0_oily.WAV
MPAM0_oily.WAV
MPAM1_oily.WAV
MPCS0_oily.WAV
MPDF0_oily.WAV
MPGL0_oily.WAV
MPLB0_oily.WAV
MPWM0_oily.WAV
MRCS0_oily.WAV
MRCZ0_oily.WAV
MREB0_oily.WAV
MRES0_oily.WAV
MRGG0_oily.WAV
MRJM3_oily.WAV
MRJM4_oily.WAV
MRJO0_oily

MTDT0_suit.WAV
MTEB0_suit.WAV
MTHC0_suit.WAV
MTLS0_suit.WAV
MTMR0_suit.WAV
MTWH0_suit.WAV
MWBT0_suit.WAV
MWEW0_suit.WAV
MWJG0_suit.WAV
MWVW0_suit.WAV
FADG0_that.WAV
FAKS0_that.WAV
FASW0_that.WAV
FAWF0_that.WAV
FCAL1_that.WAV
FCAU0_that.WAV
FCFT0_that.WAV
FCMH0_that.WAV
FCMH1_that.WAV
FCMR0_that.WAV
FCRH0_that.WAV
FDAC1_that.WAV
FDHC0_that.WAV
FDMS0_that.WAV
FDRD1_that.WAV
FDRW0_that.WAV
FEDW0_that.WAV
FELC0_that.WAV
FGJD0_that.WAV
FGMD0_that.WAV
FGWR0_that.WAV
FHES0_that.WAV
FHEW0_that.WAV
FISB0_that.WAV
FJAS0_that.WAV
FJCS0_that.WAV
FJEM0_that.WAV
FJLM0_that.WAV
FJMG0_that.WAV
FJRE0_that.WAV
FJSA0_that.WAV
FJSJ0_that.WAV
FJWB0_that.WAV
FKMS0_that.WAV
FLAS0_that.WAV
FLBW0_that.WAV
FLKD0_that.WAV
FLNH0_that.WAV
FMAF0_that.WAV
FMAH0_that.WAV
FMCM0_that.WAV
FMGD0_that.WAV
FMLD0_that.WAV
FMML0_that.WAV
FNLP0_that.WAV
FNMR0_that.WAV
FPAS0_that.WAV
FPKT0_that.WAV
FRAM1_that.WAV
FREW0_that.WAV
FRNG0_that.WAV
FSEM0_that.WAV
FSLB1_that.WAV
FSXA0_that.WAV
FTLH0_that.WAV
FUTB0_that.WAV
MABW0_that

MPGL0_water.WAV
MPLB0_water.WAV
MPWM0_water.WAV
MRCS0_water.WAV
MRCZ0_water.WAV
MREB0_water.WAV
MRES0_water.WAV
MRGG0_water.WAV
MRJM3_water.WAV
MRJM4_water.WAV
MRJO0_water.WAV
MRJR0_water.WAV
MRJS0_water.WAV
MRKO0_water.WAV
MRMS1_water.WAV
MROA0_water.WAV
MRPC0_water.WAV
MRPP0_water.WAV
MRRK0_water.WAV
MRTK0_water.WAV
MRWS1_water.WAV
MSFH1_water.WAV
MSJS1_water.WAV
MSLB0_water.WAV
MSTK0_water.WAV
MTAA0_water.WAV
MTAS1_water.WAV
MTDT0_water.WAV
MTEB0_water.WAV
MTHC0_water.WAV
MTLS0_water.WAV
MTMR0_water.WAV
MTWH0_water.WAV
MWBT0_water.WAV
MWEW0_water.WAV
MWJG0_water.WAV
MWVW0_water.WAV
FADG0_year.WAV
FAKS0_year.WAV
FASW0_year.WAV
FAWF0_year.WAV
FCAL1_year.WAV
FCAU0_year.WAV
FCFT0_year.WAV
FCMH0_year.WAV
FCMH1_year.WAV
FCMR0_year.WAV
FCRH0_year.WAV
FDAC1_year.WAV
FDHC0_year.WAV
FDMS0_year.WAV
FDRD1_year.WAV
FDRW0_year.WAV
FEDW0_year.WAV
FELC0_year.WAV
FGJD0_year.WAV
FGMD0_year.WAV
FGWR0_year.WAV
FHES0_year.WAV
FHEW0_year.WAV
FISB0_year.WAV
FJAS0_year.WAV
FJCS0_year.WAV
FJEM0_year.WAV
FJL

In [84]:
max=x_train[0][0][0] 
min=x_train[0][0][0]
for i in range(len(x_train)):
    for x in range(x_train[i].shape[0]):
        for y in range(x_train[i].shape[1]):
            if (x_train[i][x][y]<min):
                min=x_train[i][x][y]
            elif(x_train[i][x][y]>max):
                max=x_train[i][x][y]
for i in range(len(x_test)):
    for x in range(x_test[i].shape[0]):
        for y in range(x_test[i].shape[1]):
            if (x_test[i][x][y]<min):
                min=x_test[i][x][y]
            elif(x_test[i][x][y]>max):
                max=x_test[i][x][y]
feature_range=[max,min]

# TRAINING MODEL

In [76]:
sa1.train(X_train=x_train,X_test=x_test,n_epochs=50,learning_rate=0.1,save_steps=10,feature_range=feature_range)

compiling theano training functions ...
(9700,)


A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"
A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"
A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You 

training the SA model ...

epoch #1
average train batch cost = 228.987033
average test batch cost = 229.419883

epoch #2
average train batch cost = 228.674015
average test batch cost = 228.380612

epoch #3
average train batch cost = 228.422963
average test batch cost = 228.272415

epoch #4
average train batch cost = 228.181619
average test batch cost = 229.049214

epoch #5
average train batch cost = 227.831452
average test batch cost = 227.585787

epoch #6
average train batch cost = 227.535061
average test batch cost = 229.792159

epoch #7
average train batch cost = 227.477340
average test batch cost = 228.088922

epoch #8
average train batch cost = 227.316836
average test batch cost = 227.533587

epoch #9
average train batch cost = 227.086626
average test batch cost = 227.131215

epoch #10
average train batch cost = 226.901471
average test batch cost = 226.440216

epoch #11
average train batch cost = 226.405521
average test batch cost = 227.014094

epoch #12
average train batch cost =

# CREATE WORD EMBEDDINGS


In [77]:

#x=T.matrix('x')
#final=SA(x,13,100,13)
file=open('lstmae.100.final.pkl','rb')
final= pickle.load(file)

In [1]:
train_embeddings=final.create_embeddings(input_words=x_train,feature_range=feature_range)

In [85]:
train_embeddings=[]
for i in range((x_train.shape[0])):
    list=final.create_embeddings(input_words=x_train[i],feature_range=feature_range)
    train_embeddings.append(list)

A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"


embeddings...


A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"


embeddings...


A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"


...

A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"


embeddings...


A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"


embeddings...
embeddings...


A:\anaconda\lib\site-packages\theano\scan_module\scan_perform_ext.py:76: UserWarning: The file scan_perform.c is not available. This donot happen normally. You are probably in a strangesetup. This mean Theano can not use the cython code for scan. If youwant to remove this warning, use the Theano flag'cxx=' (set to an empty string) to disable all ccode generation.
  "The file scan_perform.c is not available. This do"


In [86]:
timit="word_wise_data/train_words"
train_list_embeddings=[]
train_list_words=[]
timit_db=[os.path.join(timit,p) for p in sorted(os.listdir(timit))]
for i in range(len(timit_db)):
    word=timit_db[i].split("\\")[1]
    word_from_every_speaker_path=[os.path.join(timit_db[i],p) for p in sorted(os.listdir(timit_db[i]))]
    for i in range(len(word_from_every_speaker_path)):
        (rate,sig) = wav.read(word_from_every_speaker_path[i])
        if(sig.shape[0]!=0):
            #mfcc_feat= mfcc(sig,rate)
            #train_list_embeddings.append(final.create_embeddings(input_words=mfcc_feat,feature_range=feature_range)[-1])
            train_list_words.append(word)
            #print(word_from_every_speaker_path[i].split("\\")[2])


In [87]:
timit="word_wise_data/test_words"
test_list_embeddings=[]
test_list_words=[]
timit_db=[os.path.join(timit,p) for p in sorted(os.listdir(timit))]
for i in range(len(timit_db)):
    word=timit_db[i].split("\\")[1]
    word_from_every_speaker_path=[os.path.join(timit_db[i],p) for p in sorted(os.listdir(timit_db[i]))]
    for i in range(len(word_from_every_speaker_path)):
        (rate,sig) = wav.read(word_from_every_speaker_path[i])
        if(sig.shape[0]!=0):
            #mfcc_feat= mfcc(sig,rate)
            #test_list_embeddings.append(final.create_embeddings(input_words=mfcc_feat,feature_range=feature_range)[-1])
            test_list_words.append(word)
            #print(word_from_every_speaker_path[i].split("\\")[2])


In [26]:
#if os.path.getsize('train_list_embeddings.pkl') > 0:
#    print("djkl")
f=open('train_list_embeddings.pkl', 'rb') 
train_list_embeddings=pickle.load(f)

file=open('test_list_embeddings.pkl','rb')
test_list_embeddings= pickle.load(file)

In [2]:
max_similarity=metrics.cosine_similarity(test_list_embeddings[0].reshape(1,-1),train_list_embeddings[0].reshape(1,-1))
predictions=[]
for i in range(len(test_list_embeddings)):
    max_similarity=metrics.cosine_similarity(test_list_embeddings[i].reshape(1,-1),train_list_embeddings[0].reshape(1,-1))[0][0]
    for j in range(len(train_list_embeddings)):
        similarity=metrics.cosine_similarity(test_list_embeddings[i].reshape(1,-1),train_list_embeddings[j].reshape(1,-1))[0][0]
        if(similarity>max_similarity):
            max_similarity=similarity
            similarword=train_list_words[j]
    predictions.append(similarword)       


In [89]:
len(predictions)

3528

In [90]:
len(test_list_words)

3528

In [29]:
x_train=np.asarray(train_list_embeddings)
y_train=np.asarray(train_list_words)
x_test=np.asarray(test_list_embeddings)
y_test=np.asarray(test_list_words)


In [42]:
test_labels= labelencoder_.fit_transform(y_test)

In [30]:
x_train.shape

(9700, 100)

In [20]:
from sklearn.preprocessing import LabelEncoder, OneHotEncoder

labelencoder_ = LabelEncoder()
# cifarlabels_test= labelencoder_.fit_transform(cifarlabels_test)

labels= labelencoder_.fit_transform(y_train)
# cifarlabels=to_categorical(cifarlabels)
# cifarlabels_test=to_categorical(cifarlabels_test)

In [66]:
from keras.layers import Input,Dense
from keras.models import Model

input= Input(shape=(100,))
x= Dense(64, activation='relu')(input)
# x=Dense(64,activation='relu')(x)
x=Dense(32,activation='relu')(x)


output=Dense(21)(x)



In [67]:
model = Model(input, output)
sgd = SGD(lr=1e-5, decay=1e-6, momentum=0.9, nesterov=True)
model.compile(optimizer=sgd, loss='sparse_categorical_crossentropy',metrics=['accuracy'])
model.fit(x_train, labels,
                epochs=30,
                batch_size=16,
                shuffle=True,validation_data=(x_test, test_labels))


Train on 9700 samples, validate on 3528 samples
Epoch 1/30
9700/9700 [==============================] - 1s 99us/step - loss: 8.0618 - acc: 0.0475 - val_loss: 8.0266 - val_acc: 0.0476
Epoch 2/30
9700/9700 [==============================] - 1s 62us/step - loss: 7.9996 - acc: 0.0476 - val_loss: 7.9679 - val_acc: 0.0476
Epoch 3/30
9700/9700 [==============================] - 1s 54us/step - loss: 7.9367 - acc: 0.0476 - val_loss: 7.8977 - val_acc: 0.0476
Epoch 4/30
9700/9700 [==============================] - 1s 54us/step - loss: 7.8525 - acc: 0.0476 - val_loss: 7.7957 - val_acc: 0.0476
Epoch 5/30
9700/9700 [==============================] - 0s 51us/step - loss: 7.6025 - acc: 0.0476 - val_loss: 7.0655 - val_acc: 0.0476
Epoch 6/30
9700/9700 [==============================] - 0s 51us/step - loss: 5.8008 - acc: 0.0484 - val_loss: 3.0445 - val_acc: 0.0476
Epoch 7/30
9700/9700 [==============================] - 0s 50us/step - loss: 3.0445 - acc: 0.0476 - val_loss: 3.0445 - val_acc: 0.0476
Epoch 8

In [68]:
prediction=model.predict(x_train)

In [40]:
x=argmax(prediction[0],axis=0)

# Word wise Accuracy

In [108]:
test_labels=le.transform(test_list_words)
accuracy=np.zeros(21)
classes=le.transform(le.classes_)
test_predictions=le.transform(predictions)
for i in classes:
    list_predictions=[]
    list_labels=[]
    for j in range(len(test_labels)):
        #print(test_labels[j],"test_labels")
        #print(i,"classes")
        if(test_labels[j]==i):
            list_labels.append(test_labels[j])
            list_predictions.append(test_predictions[j])
    accuracy[i]=maccuracy.accuracy_score(list_predictions,list_labels)

In [119]:
word_wise_accuracy=pd.DataFrame(accuracy.reshape(1,21),columns=le.classes_)

In [123]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(word_wise_accuracy)

all        an       ask     carry      dark  don't    greasy  \
0  0.517857  0.345238  0.553571  0.392857  0.684524  0.375  0.327381   

        had        in      like        me      oily      rag  she      suit  \
0  0.720238  0.488095  0.571429  0.255952  0.327381  0.47619  0.5  0.327381   

    that        to      wash     water      year      your  
0  0.375  0.333333  0.839286  0.755952  0.666667  0.559524

# Avg Accuracy across all words

In [ ]:
le = preprocessing.LabelEncoder()
le.fit(train_list_words)
test_labels=le.transform(test_list_words)
test_predictions=le.transform(predictions)
from sklearn.metrics import accuracy_score
#print("Training accuracy",accuracy_score(train_predictions[0],labels_train))
print("Testing accuracy:",accuracy_score(test_predictions,test_labels))


In [ ]:

test_labels=le.transform(test_list_words)

test_predictions=le.transform(predictions)
from sklearn.metrics import accuracy_score
#print("Training accuracy",accuracy_score(train_predictions[0],labels_train))
print("Testing accuracy:",accuracy_score(test_predictions,test_labels))


In [6]:
le = preprocessing.LabelEncoder()
le.fit(test_list_words)
test_labels=le.transform(test_list_words)

In [47]:
cos_similarity_between_words=np.zeros((21,21))

In [20]:
list=[]


In [26]:
len(test_list_embeddings)

3528

In [49]:
cosine_simi=0
for i in range(len(le.classes_)):
    for j in range(len(le.classes_)):
        list1=[]
        list2=[]
        if(i!=j):
            for m in range(len(test_list_words)):
                if(test_list_words[m]==le.classes_[i]):
                    list1.append(test_list_embeddings[m])
                elif(test_list_words[m]==le.classes_[j]):
                    list2.append(test_list_embeddings[m])
            print(len(list1))
            print(len(list2))
            for k in list1:
                for l in list2:
                    cosine_simi+=metrics.cosine_similarity(k.reshape(1,-1),l.reshape(1,-1))[0][0]
            cos_similarity_between_words[i][j]=cosine_simi/(len(list1)*len(list2))
            cosine_simi=0
        elif(i==j):
            for m in range(len(test_list_words)):
                if(test_list_words[m]==le.classes_[i]):
                    list1.append(test_list_embeddings[m])
            index1=0
            count=0
            cosine_simi=0
            while(index1<len(list1)):
                index2=index1+1
                while(index2<len(list1)):
                    #print(type(cosine_simi))
                    cosine_simi+=metrics.cosine_similarity(list1[index1].reshape(1,-1),list1[index2].reshape(1,-1))[0][0]
                    count+=1
                    index2+=1
                index1+=1
            cos_similarity_between_words[i][j]=cosine_simi/count
            cosine_simi=0
        

168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168
168


# COSINE SIMILIRATY B/W EVERY WORD

In [69]:
#def highlight_max():
for i in le.classes_:
    x=matrix.loc[i]
    max=x[0]
    for i in x:
        if(i>max):
            max=i
        
matrix.loc['all']
 

all       0.481156
an        0.366990
ask       0.211937
carry     0.441431
dark      0.262341
don't     0.373604
greasy    0.383678
had       0.328348
in        0.302613
like      0.206123
me        0.403732
oily      0.468846
rag       0.289390
she       0.390836
suit      0.350179
that      0.249466
to        0.393976
wash      0.242701
water     0.350056
year      0.324040
your      0.413851
Name: all, dtype: float64

In [124]:
# Yellow color here indicates the max value in that column
def highlight_max(s):
    '''
    highlight the maximum in a Series yellow.
    '''
    is_max = s == s.max()
    return ['background-color: yellow' if v else '' for v in is_max]
matrix.style.apply(highlight_max)


In [56]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(matrix)

all        an       ask     carry      dark     don't    greasy  \
all     0.481156  0.366990  0.211937  0.441431  0.262341  0.373604  0.383678   
an      0.366990  0.434228  0.248989  0.375275  0.254643  0.369682  0.348783   
ask     0.211937  0.248989  0.592474  0.215978  0.511071  0.250434  0.216350   
carry   0.441431  0.375275  0.215978  0.578438  0.296051  0.344260  0.444991   
dark    0.262341  0.254643  0.511071  0.296051  0.643980  0.278844  0.243756   
don't   0.373604  0.369682  0.250434  0.344260  0.278844  0.374871  0.286315   
greasy  0.383678  0.348783  0.216350  0.444991  0.243756  0.286315  0.522360   
had     0.328348  0.305678  0.397792  0.428204  0.328083  0.279551  0.486074   
in      0.302613  0.393284  0.280160  0.340925  0.170701  0.298401  0.383889   
like    0.206123  0.265170  0.560385  0.228417  0.575835  0.276434  0.154182   
me      0.403732  0.345696  0.220899  0.536522  0.194506  0.299473  0.497864   
oily    0.468846  0.392738  0.176108  0.526542  0.320515  0.347383  0.485707   
rag     0.289390  0.318447  0.401024  0.198635  0.341794  0.319578  0.189915   
she     0.390836  0.336698  0.238528  0.494696  0.179092  0.288304  0.508478   
suit    0.350179  0.345371  0.396410  0.449481  0.392587  0.306546  0.448364   
that    0.249466  0.271330  0.541592  0.282223  0.549496  0.283581  0.217330   
to      0.393976  0.381204  0.264761  0.527901  0.274141  0.298179  0.524051   
wash    0.242701  0.283276  0.564737  0.276607  0.647222  0.311019  0.256259   
water   0.350056  0.247467  0.122449  0.193889  0.277976  0.320133  0.062715   
year    0.324040  0.269089  0.149981  0.251280  0.377579  0.277239  0.151884   
your    0.413851  0.359005  0.136625  0.485404  0.356002  0.310307  0.466236   

             had        in      like        me      oily       rag       she  \
all     0.328348  0.302613  0.206123  0.403732  0.468846  0.289390  0.390836   
an      0.305678  0.393284  0.265170  0.345696  0.392738  0.318447  0.336698   
ask     0.397792  0.280160  0.560385  0.220899  0.176108  0.401024  0.238528   
carry   0.428204  0.340925  0.228417  0.536522  0.526542  0.198635  0.494696   
dark    0.328083  0.170701  0.575835  0.194506  0.320515  0.341794  0.179092   
don't   0.279551  0.298401  0.276434  0.299473  0.347383  0.319578  0.288304   
greasy  0.486074  0.383889  0.154182  0.497864  0.485707  0.189915  0.508478   
had     0.702723  0.362745  0.289784  0.557512  0.374144  0.222367  0.607210   
in      0.362745  0.468615  0.238914  0.387615  0.333023  0.308954  0.388245   
like    0.289784  0.238914  0.656252  0.150577  0.210293  0.444567  0.133566   
me      0.557512  0.387615  0.150577  0.602192  0.467761  0.162937  0.604579   
oily    0.374144  0.333023  0.210293  0.467761  0.585096  0.225110  0.437630   
rag     0.222367  0.308954  0.444567  0.162937  0.225110  0.457094  0.164054   
she     0.607210  0.388245  0.133566  0.604579  0.437630  0.164054  0.629332   
suit    0.551624  0.371182  0.365917  0.485495  0.422285  0.280277  0.494582   
that    0.379887  0.242223  0.579545  0.237634  0.250296  0.387197  0.235171   
to      0.525716  0.419771  0.216456  0.567718  0.505493  0.199567  0.563654   
wash    0.434320  0.211262  0.631457  0.227686  0.276420  0.388099  0.239378   
water  -0.120627  0.090647  0.260634 -0.004032  0.286838  0.329881 -0.067937   
year   -0.024578  0.105860  0.291097  0.048466  0.382283  0.270490 -0.013838   
your    0.327892  0.278348  0.214423  0.396634  0.593208  0.191426  0.358592   

            suit      that        to      wash     water      year      your  
all     0.350179  0.249466  0.393976  0.242701  0.350056  0.324040  0.413851  
an      0.345371  0.271330  0.381204  0.283276  0.247467  0.269089  0.359005  
ask     0.396410  0.541592  0.264761  0.564737  0.122449  0.149981  0.136625  
carry   0.449481  0.282223  0.527901  0.276607  0.193889  0.251280  0.485404  
dark    0.392587  0.549496  0.274141  0.647222  0.277976  0.377579  0.356002  
don't   0.306546 

In [78]:
she_word_embeddings=[]
dark_word_embeddings=[]
cosine_simi=[]
for i in range(len(test_list_embeddings)):
    if(test_list_words[i]=='dark'):
        she_word_embeddings.append(test_list_embeddings[i])
    #elif(test_list_words[i]=='dark'):
    #    dark_word_embeddings.append(test_list_embeddings[i])
index1=0
count=0
while(index1<len(she_word_embeddings)):
    index2=index1+1
    while(index2<len(she_word_embeddings)):
        count+=1  
        cosine_simi.append(metrics.cosine_similarity(she_word_embeddings[index1].reshape(1,-1),she_word_embeddings[index2].reshape(1,-1)))
        index2+=1
    index1+=1
sum=0
for i in range(len(cosine_simi)):
    sum+=cosine_simi[i]
avg=sum/count
print("AVG cosine similarity between she and dark words:",avg)      
        
        
    

AVG cosine similarity between she and dark words: [[ 0.64397982]]


168

In [79]:
print(count)

14028


In [42]:
metrics.cosine_similarity(train_list_embeddings[0].reshape(1,-1),train_list_embeddings[1].reshape(1,-1))[0][0]

0.66927237091996727

In [2]:
cosine_simi=[]
for i in range(len(she_word_embeddings)):
    for j in range((len(she_word_embeddings))):
        if(i!=j):
            cosine_simi.append(m.cosine_similarity(she_word_embeddings[i].reshape(1,-1),she_word_embeddings[j].reshape(1,-1)))
sum=0
for i in range(len(cosine_simi)):
    sum+=cosine_simi[i]
avg=sum/len(cosine_simi)
print("AVG cosine similarity between she and she words:",avg)      
        
        
    

AVG cosine similarity between she and she words: 0.66891783


In [63]:
simi_dark_she=m.cosine_similarity(train_list_embeddings[2000].reshape(1,-1),train_list_embeddings[6100].reshape(1,-1))
simi_she_she=m.cosine_similarity(train_list_embeddings[6101].reshape(1,-1),train_list_embeddings[6102].reshape(1,-1))
simi_wash_water=m.cosine_similarity(train_list_embeddings[8000].reshape(1,-1),train_list_embeddings[8500].reshape(1,-1))
simi_wash_wash=m.cosine_similarity(train_list_embeddings[8000].reshape(1,-1),train_list_embeddings[8001].reshape(1,-1))
print("dark_she word embeddings similarity:",simi_dark_she)
print("she_she word embeddings similarity:",simi_she_she)
print("wash_water word embeddings similarity:",simi_wash_water)
print("wash_wash word embeddings similarity:",simi_wash_wash)

dark_she word embeddings similarity: [[ 0.14906119]]
she_she word embeddings similarity: [[ 0.83426388]]
wash_water word embeddings similarity: [[ 0.36964266]]
wash_wash word embeddings similarity: [[ 0.7215534]]
